### 중앙 기사 데이터 수집
- scrapy에서 selenium 사용해보기
- pipeline 사용하기

#### 1. 프로젝트 생성

In [1]:
!scrapy startproject it_donga_article

New Scrapy project 'it_donga_article', using template directory '/Users/seogihyun/opt/anaconda3/lib/python3.8/site-packages/scrapy/templates/project', created in:
    /Users/seogihyun/Documents/fcdss15/it_donga_article

You can start your first spider with:
    cd it_donga_article
    scrapy genspider example example.com


In [2]:
!tree it_donga_article/

it_donga_article/
├── it_donga_article
│   ├── __init__.py
│   ├── items.py
│   ├── middlewares.py
│   ├── pipelines.py
│   ├── settings.py
│   └── spiders
│       └── __init__.py
└── scrapy.cfg

2 directories, 7 files


#### 2. xpath 찾기
- article links: 

In [3]:
import scrapy, requests, json
from scrapy.http import TextResponse
from selenium import webdriver

In [87]:
#경제
url = "https://it.donga.com/news/?page=1"
# url = "https://it.donga.com/31301/"
headers = {"User-Agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.67 Safari/537.36"}
req = requests.get(url, headers=headers)
req, url

(<Response [200]>, 'https://it.donga.com/news/?page=1')

In [88]:
response = TextResponse(req.url, body=req.text, encoding="utf-8")

In [89]:
title = response.xpath('/html/body/main/div/div[1]/ul/li/a/div/h5/text()').extract()
date = response.xpath('/html/body/main/div/div[1]/ul/li/a/div/div[1]/div/time/text()').extract()
link = response.xpath('/html/body/main/div/div[1]/ul/li/a/@href').extract()
title, link, date

(['\n              스타트업 방법론의 무한 확장, 로컬 문화기획 영역까지 전파\n            ',
  "\n              경기도, 26~29일 퓨처쇼 2020 개최··· '집에서 체험하는 4차 산업의 장'\n            ",
  '\n              [주간투자동향] 오늘의집, 770억 원 규모의 투자 유치\n            ',
  '\n              네이버 PC 검색, 모바일과 같게 개편\n            ',
  '\n              [뉴스줌인] 레퍼런스 그래픽카드란?\n            ',
  "\n              [IT신상공개] 이게 망원경이야, 카메라야? 캐논 '파워샷 줌'\n            ",
  "\n              [서평] 2021년 유튜브/미디어 트렌드를 짚어본다, '유튜브 트렌드2021'\n            ",
  '\n              [기술창업] 서부경기문화창조허브 - 와이캣 전성우 대표 "스마트폰 거치링, 이제 꺼내지 말고 미세요"\n            ',
  '\n              엔비디아의 8부 능선은 넘었다··· AMD 라데온 RX 6000 시리즈 정식 출시\n            ',
  '\n              [기술창업] 서부경기문화창조허브 - 홀로 정광현,주진 공동대표 "상상대로 커스터마이징하라"\n            '],
 ['/31301/',
  '/31298/',
  '/31297/',
  '/31293/',
  '/31292/',
  '/31294/',
  '/31291/',
  '/31286/',
  '/31288/',
  '/31287/'],
 ['2020.11.24.',
  '2020.11.23.',
  '2020.11.23.',
  '2020.11.22.',
  '2020.11.22.',
  '2020.11.22.',
  '2020.11.22.',
  '2020.11.

In [90]:
contents = response.xpath('/html/body/main/div/div[1]/div[2]/article/p/text()').extract()
contents, response.url

([], 'https://it.donga.com/news/?page=1')

In [ ]:
/html/body/main/div/div[1]/div[2]/article/p[9]/text()
class="article"

In [123]:
# selenium 사용 : xpath

In [124]:
options = webdriver.ChromeOptions()
options.add_argument("headless")
driver = webdriver.Chrome(options=options)

In [125]:
# content : title, category, content

In [139]:
import scrapy
import requests
from scrapy.http import TextResponse
url = 'https://it.donga.com/31301/'
req = requests.get(url)
response = TextResponse(req.url, body=req.content, encoding='utf-8')
content = response.xpath('/html/body/main/div/div[1]/div[2]/article/p"/text()').extract()
content = "".join(content)
title = response.xpath('//*[@id="news_title_text_id"]/text()').extract()[0]

In [53]:
for num in range(1,17):
    url = 'https://it.donga.com/news/?page={}'.format(num)
    print(url)

https://it.donga.com/news/?page=1
https://it.donga.com/news/?page=2
https://it.donga.com/news/?page=3
https://it.donga.com/news/?page=4
https://it.donga.com/news/?page=5
https://it.donga.com/news/?page=6
https://it.donga.com/news/?page=7
https://it.donga.com/news/?page=8
https://it.donga.com/news/?page=9
https://it.donga.com/news/?page=10
https://it.donga.com/news/?page=11
https://it.donga.com/news/?page=12
https://it.donga.com/news/?page=13
https://it.donga.com/news/?page=14
https://it.donga.com/news/?page=15
https://it.donga.com/news/?page=16


In [ ]:
url = "http://it.chosun.com/svc/list_in/list.html?catid=A&pn=1"
headers = {"User-Agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.67 Safari/537.36"}
req = requests.get(url, headers=headers)
req

#### 3. itmes.py

In [91]:
%%writefile it_donga_article/it_donga_article/items.py
import scrapy

class ItDongAArticleItem(scrapy.Item):
    title = scrapy.Field()
    link = scrapy.Field()
    p_date = scrapy.Field()
    content = scrapy.Field()
    press_agency = scrapy.Field()
    img = scrapy.Field()

Overwriting it_donga_article/it_donga_article/items.py


#### 4. spider.py
- selenium 사용

In [107]:
%%writefile it_donga_article/it_donga_article/spiders/spider.py

import scrapy
from it_donga_article.items import ItDongAArticleItem

class ArticleSpider(scrapy.Spider):
    name = "ItDongAArticle"
    allow_domain = ["https://it.donga.com/"]

    def __init__(self, **kwargs):
        self.start_urls = ["https://it.donga.com/news/?"]
        super().__init__(**kwargs)
    
    def parse(self,response):
        breed_urls = []
        for page in range(1,171):
            breed_urls.append(response.url + "?page={}".format(page))
        for url in breed_urls:
            yield scrapy.Request(url=url,callback=self.parse_sub_urls)


    def parse_sub_urls(self,response):
        links = response.xpath('/html/body/main/div/div[1]/ul/li/a/@href').extract()
        for link in links:
            link = "https://it.donga.com"+link
            yield scrapy.Request(link, callback=self.parse_content)
    
    def parse_content(self, response):
        item = ItDongAArticleItem()
        item["title"] = response.xpath('/html/body/main/div/div[1]/div[2]/article/header/h1/text()').extract()[0]
        item["p_date"] = response.xpath('/html/body/main/div/div[1]/div[2]/article/header/div[2]/div[2]/time/text()').extract()[0]
        content = response.xpath('/html/body/main/div/div[1]/div[2]/article/p/text()').extract()
        item['content'] = "".join(content)
        item['press_agency'] = 'it_donga'
        item["link"] = response.url
        yield item

Overwriting it_donga_article/it_donga_article/spiders/spider.py


#### 5. scrpay 프로젝트 실행
- windows 사용하는 경우에는 직접 cli 환경에서 실행
- scrapy crawl NaverArticle -o article.csv
- robots.txt 문제 -> settings.py 수정 ( True -> False )

In [108]:
%%writefile run.sh
rm it_donga_article/it_donga_article.csv
cd it_donga_article
scrapy crawl ItDongAArticle -o it_donga_article.csv

Overwriting run.sh


In [109]:
!source run.sh

2020-11-24 20:04:18 [scrapy.utils.log] INFO: Scrapy 2.4.0 started (bot: it_donga_article)
2020-11-24 20:04:18 [scrapy.utils.log] INFO: Versions: lxml 4.5.2.0, libxml2 2.9.10, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 20.3.0, Python 3.8.3 (default, Jul  2 2020, 11:26:31) - [Clang 10.0.0 ], pyOpenSSL 19.1.0 (OpenSSL 1.1.1g  21 Apr 2020), cryptography 2.9.2, Platform macOS-10.15.7-x86_64-i386-64bit
2020-11-24 20:04:18 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
2020-11-24 20:04:18 [scrapy.crawler] INFO: Overridden settings:
{'BOT_NAME': 'it_donga_article',
 'NEWSPIDER_MODULE': 'it_donga_article.spiders',
 'ROBOTSTXT_OBEY': True,
 'SPIDER_MODULES': ['it_donga_article.spiders']}
2020-11-24 20:04:18 [scrapy.extensions.telnet] INFO: Telnet Password: 12010bbe3a178d3b
2020-11-24 20:04:18 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.memusa

2020-11-24 20:04:22 [scrapy.core.scraper] DEBUG: Scraped from <200 https://it.donga.com/30707/>
{'content': '[IT동아 남시현 기자] 신종코로나바이러스(이하 코로나19) 이전에 비대면이라 하면, 서로 만나지 않고 진행되는 '
            '서비스의 범주를 벗어나진 않았다. 하지만 이제는 사람이 물리적으로 접촉하는 것 자체를 줄여주는 거의 모든 서비스를 '
            '비대면 서비스라 한다. 대표적으로 화상 회의나 원격 근로, 사이버 강의 등 컴퓨터를 활용한 비대면 서비스가 있으며, '
            '코로나 19 이후로는 유통, 금융, 의료 등 산업 전반으로 확장하고 있다.그렇다 보니, 화상 회의나 교육 목적의 웹캠 '
            '수요도 크게 증가하고 있다. 웹캠이란, 컴퓨터와 연결하는 카메라로, 코로나19 이전까지만 해도 화상 회의나 유튜버 등 '
            '널리 쓰이던 물건은 아니었지만, 비대면 서비스가 일상이 되면서 너도나도 웹캠을 필요로 하고 있다. 노트북이라면 웹캠을 '
            '내장한 모델이 많아 큰 문제가 없지만, 데스크톱이라면 별도로 웹캠을 갖춰야 하고, 하드웨어 설정도 잡아주어야 한다. '
            '로지텍 스트림캠(Logitech STREAMCAM)을 기준으로 웹캠 고르는 방법부터 활용 방법까지 짚어드린다.웹캠을 '
            '선택할 때 중점적으로 살펴보아야 할 것은 해상도다. 방송이나 회의 주재가 목적이라면 해상도가 우선이고, 아니라면 '
            '가격을 보자. 해상도 보는 방법은 텔레비전과 비슷하다. 현재 출시되고 있는 웹캠 해상도는 '
            'FHD(1,920x1,080) 해상도, 그리고 4K(3,840x2,160) 두 가지가 대다수며, 4K 해상도가 FHD '
            '대비 4배 더 높다. 대신 그만큼 가격 차이도 크

2020-11-24 20:04:22 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://it.donga.com/30712/> (referer: https://it.donga.com/news/?page=34)
2020-11-24 20:04:22 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://it.donga.com/30757/> (referer: https://it.donga.com/news/?page=31)
2020-11-24 20:04:22 [scrapy.core.scraper] DEBUG: Scraped from <200 https://it.donga.com/30750/>
{'content': '[IT동아 김영우 기자] IT동아 편집부에는 하루에만 수십 건을 넘는 보도자료가 온다. 대부분 새로운 제품, 혹은 '
            '서비스 출시 관련 소식이다. IT동아는 이 중에 독자들에게 도움이 될 만한 것 몇 개를 추려 기사화를 한다. 다만, '
            '기업에서 보내준 보도자료 원문에는 전문 용어, 혹은 해당기업에서만 쓰는 독자적인 용어가 다수 포함되기 마련이다. 이런 '
            "용어에 익숙하지 않은 독자를 위해 IT동아는 보도자료를 해설하는 기획기사인 '뉴스 줌인'을 준비했다.출처: "
            '와사비망고(2020년 7월 10일)제목: 와사비망고! 43형 VA패널 HDR UHDTV “ZEN U430 UHDTV '
            'MAX HDR” 출시!요약: ㈜와사비망고가 43인치형 TV인 ‘ZEN U430 UHDTV MAX HDR’를 출시했다. '
            '본 제품은 VA 패널을 탑재하고 HDR 기능을 지원하며 10비트 컬러를 지원해 생동감 있는 영상을 구현한다. HDMI '
            '단자 3개, USB 단자 2개 등을 갖췄으며 이외에도 문자 가독성을 높인 4:4:4 크로마

2020-11-24 20:04:22 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://it.donga.com/30758/> (referer: https://it.donga.com/news/?page=31)
2020-11-24 20:04:22 [scrapy.core.scraper] DEBUG: Scraped from <200 https://it.donga.com/30712/>
{'content': '[IT동아 강형석 기자] 2020년 7월 1일, 아우디는 순수 개발한 전기차 ‘아우디 이-트론 55 콰트로(Audi '
            'e-tron 55 quattro)’를 공개했다. 360마력 가량의 출력에 전기차임에도 사륜구동 기술인 '
            '콰트로(quattro) 등을 적용한 점이 특징이다. 높은 수준의 주행 및 안전 관련 기능과 스마트폰 연결성도 '
            '두드러진다. 아우디의 주행 기술 완성도에 스마트폰 연결성까지 두루 갖춘 셈이다.최근 전동화 차량 출시에 박차를 가하고 '
            '있는 아우디폭스바겐 그룹의 프리미엄 브랜드의 전기차이다 보니 매체의 관심도 높았다. 아우디 역시 관심에 보답하고자 '
            '했는지 국내 자동차 시장의 전동화 전환 가속화를 위해 충전 시설 확충 및 다양한 서비스를 진행할 예정이라는 점을 '
            '강조했다.간단한 차량 발표 이후, 질의응답 시간이 이어졌다. 이 자리에는 제프 매너링 아우디 코리아 대표 및 아우디 '
            '코리아 임원이 참석했다. 약 20여 분 가량의 질의응답 시간에서 어떤 이야기들이 나왔는지 간단히 정리했다. : 이 '
            '차량의 장점은 양보가 없는 완전 제 기능을 하는 전기차와 SUV라는 것이다. 따라서 특정 소비자가 아니라 모두가 공략 '
            '대상이다. 이-트론 외에도 한국 시장에서의 우리 전략을 언급하자면 프리미엄 브

2020-11-24 20:04:22 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://it.donga.com/30756/> (referer: https://it.donga.com/news/?page=31)
2020-11-24 20:04:22 [scrapy.core.scraper] DEBUG: Scraped from <200 https://it.donga.com/30758/>
{'content': '[IT동아 권명관 기자] 환경 보호 방법은 규제를 통한 억제가 아닌, 수요 주체의 능동적인 태도 변화에 있다. 전 '
            '인류 스스로가 환경을 보호할 수 있는 소비재를 사용하고, 소비 자원을 올바르게 순환할 수 있도록 적절하게 폐기해야 '
            '한다. 친환경 제품 사용이나 재사용, 그리고 재활용 같은 방식도 있지만, 최근에는 낡거나 버려진 물건을 가공해 새 '
            '가치로 재창출하는 업사이클링(Upcycling)을 주목하는 이유다.재활용을 통해 버리는 자원을 줄이면서 새로운 가치를 '
            '창조하는 것은 쉽지 않다. 단순 재활용이 아니라 상품성까지 갖춰야 한다. 어렵지만, 이러한 과정을 거쳐 환경 오염을 '
            '줄이고, 제품을 생산하는 과정에서 또 다른 부가가치를 창출할 수 있다. 업사이클링을 비롯한 친환경 제품 관련 시장은 '
            '환경 보호와 함께 경제적 실익이라는 두 마리 토끼를 잡을 수 있다. 때문에 각국 정부가 주도적으로 시장 성장을 '
            "장려하고 있다.경기콘텐츠진흥원과 광명경기문화창조허브가 추진하고 있는 '2020 환상마켓(온라인 에코 플리마켓)'사업도 "
            "그 중 하나다. 2020 환상마켓은 '지구에게 환심사기'라는 컨셉으로 우리 삶의 터전인 지구를 위한 친환경 제품을 "
            '생산·소비하기 위한 시장을 구축하는 사업이다. 지난 5월 31

...

2020-11-24 20:05:08 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://it.donga.com/31194/> (referer: https://it.donga.com/news/?page=7)
2020-11-24 20:05:08 [scrapy.core.scraper] DEBUG: Scraped from <200 https://it.donga.com/31184/>
{'content': '[IT동아 남시현 기자] 사회적 가치가 긍정적인 현상으로 거듭나기 위해서는 구성원 모두에게 선한 영향력이 미쳐야 '
            '한다. 이를 실현하려면 사회적 가치가 사회 전반에 선순환하는 구조가 마련되어야 하는데, 구체적으로 어떻게 동작하는 '
            '것일까? “예술과 대중의 간극을 줄이자”를 모토로 활동하는 패션 브랜드 얼킨(ul:kin)의 사례를 보면 이해가 '
            '빠르다. 얼킨은 버려지는 자재를 기반으로 만든 업사이클링 패션 제품에 신진작가의 회화 작품을 그려내 새로운 가치를 '
            '부여한다. 버려지는 즉시 환경을 오염시켰을 재료는 회화 작품을 품으며 세상에 단 하나밖에 없는 작품으로 재탄생하고, '
            '쉽게 버려졌을 신진 작가의 습작이 누군가의 손에서 그 생명을 이어나간다.더 나아가, 얼킨은 업사이클링 제품 판매로 '
            '발생하는 수익을 바탕으로 작가들에게 로열티를 지급하고, 이들이 새 캔버스나 미술 재료를 구입하고, 미술 전시회 등을 '
            '펼칠 수 있도록 도움으로써 미술 산업에 기여한다. 얼킨의 사례가 시사하는 바는 잘 만든 생태계는 어떤 식으로든 모두가 '
            '윈윈하는 구조를 만들 수 있다는 점이다. 이처럼 업사이클링은 어떤 아이템을 어떻게 구상하는가에 따라 지구를 지키고, '
            '우리 사회를 더욱 비옥하게 만든다. 하지만 업사이클링 생태계도 그

            '하는지, 가격은 적당한지, 또 수익/손실은 어느 정도 기대할 수 있을지 체크하기엔 너무 많은 시간과 손품이 들어간다. '
            "머신러닝 기술을 토대로 자신의 투자성향에 맞는 종목과 파트너를 매칭해주는 온라인 플랫폼 '올라(HOLA!)'가 "
            '이들에게 도움이 된다. 올라 플랫폼은 별도 앱이 아닌, 스마트폰의 웹브라우저(구글 크롬, 네이버, 다음 앱 등)를 '
            '열고 올라 홈페이지 주소로 접속하면 된다. 이후 간단한 회원가입 절차를 거쳐, 투자 성향을 묻는 몇 가지 질문에 '
            '답하면 곧바로 사용자의 투자성향을 진단한다. (네이버나 카카오 계정이 있으면 가입 단계를 더 줄일 수 있다.)이후 '
            '투자성향에 적합한 추천 종목과 리스트 등이 제공되는데, 각 종목 정보는 기본적으로 모자이크로 제한 표시되며, 종목 '
            '성향과 목표수익률이 마음에 들면, 최소 0원에서 최대 3만 원 사이로 종목을 개별 구매할 수 있다. 올라는 서비스 '
            '런칭 기념으로 모든 회원가입자에게 10만 포인트가 무료 제공되는데, 이 포인트로 추천리스트 중 원하는 종목 정보를 '
            '충분히 참고하고 주식 구매 결정을 내리면 된다. 무료 포인트 소진 후에는 원하는 결제 포인트 만큼 신용카드 또는 '
            '실시간 계좌이체로 바로 추가 구매해 이용할 수 있다. 포인트 없이 무료 열람이 가능한 전문가들의 종목도 제공된다. '
            '이들 전문가는 주요 주식방송(MTN 등)에 출연하며 금융권에서 오랜 경험이 있으며, 각 전문가들의 종목추천 성공/실패 '
            '이력, 평균 수익률, 승률 등을 한 눈에 볼 수 있어, 어느 전문가의 어떤 종목을 열람할지 선택하는데 도움이 된다. '
            '예를 들어, 우리나라 최대 우량주인 삼성의 경우 주식을 잘 모르는 이

            '목표다.: 코로나19 사태로 인해 진행에 다���의 어려움이 있긴 했지만 그런 와중에도 SKT측에서 도움을 주려고 '
            '노력하는 것이 느껴졌다. 특히 전문가와의 연계를 통한 멘토링 및 강연 프로그램은 제법 유용했다. : 저도 식당을 '
            '운영해 봤지만 요즘 자영업자들은 일하는 시간에 비해 수익은 너무 적다. 더욱이 마케팅이나 재무, 회계, 인사관리 등을 '
            '모두 점주가 해야 하는 경우가 많아 더욱 안타깝다. 우리는 식자재 구매와 관련한 최적의 경로를 찾고, 높은 품질의 '
            '물건을 좋은 가격으로 이용할 수 있도록 돕는 것으로 식당 사장님들의 고민을 덜어드리고자 한다. 그들의 꿈과 열정을 '
            '응원하는 동반자가 될 것이다. 글 / IT동아 김영우(pengo@itdonga.com)',
 'link': 'https://it.donga.com/31201/',
 'p_date': '2020.10.29.',
 'press_agency': 'it_donga',
 'title': "[스타트업-ing] 점주님에게 '딱'인 식자재 찾아드립니다 ‘오더히어로’"}
2020-11-24 20:05:08 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://it.donga.com/31234/> (referer: https://it.donga.com/news/?page=5)
2020-11-24 20:05:08 [scrapy.core.scraper] DEBUG: Scraped from <200 https://it.donga.com/31199/>
{'content': '[IT동아 장현지 기자] 가상현실(VR), 증강현실(AR) 및 SNS 등 크고 작은 기술의 발전/보급을 활용하여, '
            '사회적 문제를 해결하거나 대중에게 조금 더 친밀히 다가가 필요한 제품을 공급하려는 스타트업이 있다. 하지만 대기

2020-11-24 20:05:08 [scrapy.core.scraper] DEBUG: Scraped from <200 https://it.donga.com/31205/>
{'content': '[IT동아 권명관 기자] 콘텐츠가 경쟁력이 되는 시대다. 우리나라의 K-Pop, 드라마, 방송, 게임 등의 콘텐츠는 '
            '이미 세계적인 트렌드로 자리잡았고 구글, 애플, 아마존과 같은 해외의 기업들도 모바일 뿐만 아니라 OTT서비스로 '
            '콘텐츠 사업에 뛰어들며 콘텐츠 경쟁이 치열해지고 있는 상황이다. 문화체육관광부(장관 박양우)와 한국콘텐츠진흥원(원장 '
            '김영준, 이하 콘진원)은 콘텐츠 창작자들이 경쟁력을 갖출 수 있도록 융합콘텐츠 분야 아이디어를 지원하는 ‘아이디어 '
            "융합팩토리'를 2014년부터 운영하고 있다. 지속가능한 콘텐츠의 창작 및 창업 생태계 구축으로 융합콘텐츠의 성장을 "
            '위한 기반을 마련하기 위함이다. 올해에는 ‘팩토리랩(융합 콘텐츠 및 응용기술 분야, 32팀)’, '
            '‘크리에이터랩(온라인·디지털 뉴미디어 콘텐츠 분야, 21팀)’, ‘론칭랩(아이디어 융합팩토리 수료자 후속 사업화 '
            '지원, 23팀)’ 등 3개 분야로 나눠 참가팀을 모집해 진행 중이다.아이디어 융합팩토리는 지난 2014년부터 현재까지 '
            '총 691건의 아이디어를 발굴하고, 콘텐츠 제작활동비와 맞춤형 멘토링을 지원했다. 그 결과 말레이시아에서 한국을 '
            '알리는 유튜브 채널 ‘블라이미(Blimey)’는 2017년 아이디어 융합팩토리에 참가할 당시 500명이었던 구독자 '
            '수가 37만 명에 도달해 현재 약 55만명으로 성장했으며, 2019년 론칭랩에 참여해 굿즈 제작 등 커머스 서비스로 '
            '사업을 확장하는 성과를 올렸다. 또한, 맞춤형 당뇨 관

2020-11-24 20:05:08 [scrapy.core.scraper] DEBUG: Scraped from <200 https://it.donga.com/31234/>
{'content': '[IT동아]지난 2019년 4월, 대한민국은 세계 최초로 5G 이동통신 서비스를 시작했다. 비록 서브6(sub-6) '
            '주파수, 즉 6GHz 이하의 주파수를 먼저 상용화하였지만, 이동통신 선진국으로서 공격적인 면모를 전 세계에 알릴 수 '
            "있었다. 미국은 우리나라보다 늦게 5G 서비스를 시작했으나, '진정한 5G'라 할 수 있는 밀리미터파 주파수로 "
            '서비스를 개시했다. 물론 우리나라 역시 밀리미터파 5G 서비스를 시작하려 준비하고 있고, 머지않아 LTE와는 차별된 '
            '초고속 5G 이동통신 시대가 본격적으로 열리리라 기대되는 상황이다.밀리미터파 주파수는 기존 CDMA나 LTE '
            '주파수보다 10배 이상 높은 주파수로서, 5G 통신에서는 주로 28GHz와 39GHz 대역을 사용한다. 이는 대규모 '
            '이동통신에 사용된 적이 없던 주파수인데, 주파수가 높은 만큼 많은 기술적 난관이 존재한다. 파장이 매우 짧기 때문에 '
            '안테나 및 회로 설계가 어렵고, 선로 간의 간섭도 훨씬 심하며, 손실도 크기 때문에 신호를 멀리 보내기가 힘들다. 그 '
            '대신, 초광대역 통신이 가능해, 기존 이동통신과는 차별된 속도를 발휘한다. 이러한 밀리미터파 5G 통신을 이용하기 '
            '위한 모바일 기기 역시 우리나라가 세계 시장을 주도하고 있다. 한국은 세계 최초의 5G 스마트폰과 태블릿을 '
            "출시했으며, 특히 미국시장에 'mm-wave 5G' 스마트폰을 공급함으로써 5G 시대를 열였다. 여기서 한 가지 "
            '재미있는 사실은, 세계 최초의 밀리미터파 5G

In [110]:
import pandas as pd

In [111]:
df = pd.read_csv("it_donga_article/it_donga_article.csv")
# [df['p_date'].str.split(" ")[9] if "수정" in df else df['p_date'].str.split(" ")[1][1]]

In [112]:
len(df)

1700

#### 6. pipelines 사용
- 크롤링한 데이터를 mongodb에 저장하기 : pymongo 사용
- 크롤링한 데이터에서 특정한 키워드가 있는 기사가 수집되면 slack 메신저로 기사 내용과 링크 전송하기
    - slack 메신저의 incoming webhook은 1초에 1번 사용가능 -> time.sleep(1) 사용

In [79]:
# pymongo 사용

In [81]:
!pip install pymongo

     |████████████████████████████████| 379 kB 597 kB/s eta 0:00:01


In [82]:
import pymongo

In [110]:
client = pymongo.MongoClient("mongodb://13.124.218.175:27017")
db = client.naver_article
collection = db.article
collection.insert({"title" : "scrapy"})

<ipython-input-110-c2b5cde32181>:4: DeprecationWarning: insert is deprecated. Use insert_one or insert_many instead.
  collection.insert({"title" : "scrapy"})


ObjectId('5fae20a8d089f869fd8468f9')

In [111]:
%%writefile naver_article/naver_article/mongodb.py
import pymongo
client = pymongo.MongoClient("mongodb://13.124.218.175:27017")
db = client.naver_article

collection = db.article
collection.insert

Overwriting naver_article/naver_article/mongodb.py


In [105]:
# pipeline 추가

In [91]:
# pipeline 사용 설정 : settings.py

In [ ]:
# 중간에 #ITEM_PIPELINES #제거 , 300

In [108]:
!pwd

/Users/seogihyun/Documents/fcdss15


In [27]:
elements = driver.find_elements_by_xpath('//*[@id="contents"]/div[1]/div[2]/ul > li')

NameError: name 'driver' is not defined